**Code from:**  
[【Optuna】Optuna Tutorial with Pytorch](https://nodaki.hatenablog.com/entry/2019/04/01/203209)(Japanese)

In [0]:
import torch
import torchvision
import numpy as np
import matplotlib.pyplot as plt
import tqdm

In [4]:
BATCH_SIZE = 256
transform = torchvision.transforms.Compose([
    torchvision.transforms.ToTensor(),
    torchvision.transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])

train_set = torchvision.datasets.CIFAR10('.', train=True, transform=transform,download=True)
test_set = torchvision.datasets.CIFAR10('.', train=False, transform=transform, download=True)

train_loader = torch.utils.data.DataLoader(train_set, batch_size=BATCH_SIZE, shuffle=True)
test_loader = torch.utils.data.DataLoader(test_set, batch_size=BATCH_SIZE, shuffle=False)

Extracting ./cifar-10-python.tar.gz to .
Files already downloaded and verified


In [0]:
class Net(torch.nn.Module):
  def __init__(self):
    super().__init__()
    self.conv1 = torch.nn.Conv2d(3,16,3)
    self.bn1 = torch.nn.BatchNorm2d(16)
    self.conv2 = torch.nn.Conv2d(16,32,3)
    self.bn2 = torch.nn.BatchNorm2d(32)
    self.conv3 = torch.nn.Conv2d(32, 10, 3)
    self.bn3 = torch.nn.BatchNorm2d(10)

  def forward(self,x):
    x = torch.nn.functional.max_pool2d(torch.nn.functional.relu(self.bn1(self.conv1(x))),2)
    x = torch.nn.functional.max_pool2d(torch.nn.functional.relu(self.bn2(self.conv2(x))),2)
    x = torch.nn.functional.max_pool2d(torch.nn.functional.relu(self.bn3(self.conv3(x))),2)
    x = torch.nn.functional.adaptive_avg_pool2d(x, output_size=(1,1))
    return x.view(-1, 10)

In [0]:
def train(model, device, train_loader, optimizer, criterion):
  # trian 1 epoch
  model.train()
  for data, target in tqdm.notebook.tqdm(train_loader):
    data, target = data.to(device), target.to(device)

    optimizer.zero_grad()
    output = model(data)
    loss = criterion(output, target)
    loss.backward()
    optimizer.step()

def evaluate(model, device, test_loader):
  model.eval()
  correct = 0
  with torch.no_grad():
    for data, target in test_loader:
      data, target = data.to(device), target.to(device)
      output = model(data)
      _, predicted = torch.max(output.data, 1)
      correct += (predicted == target).sum().item()
  accuracy = 1 - correct / len(test_loader.dataset)
  return accuracy

### Optuna

In [18]:
!pip install optuna

#### How to use Optuna
There are **5 ways** to set parameters.
```python
## 1. Categorical 
optimizer = trial.suggest_categorical('optimizer', ['MomentumSGD', 'Adam'])

## 2. Int 
num_layers = trial.suggest_int('num_layers', 1, 3)

## 3. Uniform
dropout_rate = trial.suggest_uniform('dropout_rate', 0., 1.)

## 4. Loguniform
learning_rate = trial.suggest_loguniform('learning_rate',1e-5, 1e-2)

## 5. Discrete-uniform
drop_path_rate = trial.suggest_discrete_uniform('drop_path_rate',0., 1., 0.1)


```

In [0]:
import optuna
def get_optimizer(trial, model):
  weight_decay = trial.suggest_loguniform('weight_decay', 1e-10, 1e-3)
  adam_lr = trial.suggest_loguniform('adam_lr', 1e-5, 1e-1)

  optimizer = torch.optim.Adam(model.parameters(), lr = adam_lr, weight_decay = weight_decay)
  return optimizer

In [0]:
EPOCH = 5

def objective(trial):
  device = 'cuda:0' if torch.cuda.is_available() else 'cpu'

  model = Net().to(device)
  optimizer = get_optimizer(trial, model)
  criterion = torch.nn.CrossEntropyLoss()

  for epoch in range(EPOCH):
    train(model, device, train_loader, optimizer, criterion)

  accuracy = evaluate(model, device, test_loader)

  return accuracy


In [27]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100, )

[I 2020-04-06 11:15:51,596] Finished trial#0 with value: 0.6414 with parameters: {'weight_decay': 0.00026530122589646306, 'adam_lr': 2.0771766203128445e-05}. Best is trial#0 with value: 0.6414.


[I 2020-04-06 11:16:40,411] Finished trial#1 with value: 0.3526 with parameters: {'weight_decay': 1.3596455127920273e-06, 'adam_lr': 0.009504140289128849}. Best is trial#0 with value: 0.6414.


[I 2020-04-06 11:17:29,096] Finished trial#2 with value: 0.42710000000000004 with parameters: {'weight_decay': 5.108506102812902e-10, 'adam_lr': 0.0005048521870660473}. Best is trial#0 with value: 0.6414.


[I 2020-04-06 11:18:18,421] Finished trial#3 with value: 0.5510999999999999 with parameters: {'weight_decay': 1.8496236482789695e-09, 'adam_lr': 6.287995901079176e-05}. Best is trial#0 with value: 0.6414.


[I 2020-04-06 11:19:07,768] Finished trial#4 with value: 0.6436 with parameters: {'weight_decay': 8.229797540941777e-09, 'adam_lr': 1.9799726665720826e-05}. Best is trial#4 with value: 0.6436.


...

[I 2020-04-06 12:27:06,710] Finished trial#95 with value: 0.6705 with parameters: {'weight_decay': 1.5510261682650704e-08, 'adam_lr': 1.4842283836323417e-05}. Best is trial#64 with value: 0.7177.


[I 2020-04-06 12:27:48,801] Finished trial#96 with value: 0.7092 with parameters: {'weight_decay': 6.276029589151382e-07, 'adam_lr': 1.0121283339517891e-05}. Best is trial#64 with value: 0.7177.


[I 2020-04-06 12:28:31,028] Finished trial#97 with value: 0.3832 with parameters: {'weight_decay': 7.243300406466695e-07, 'adam_lr': 0.0014976992073803663}. Best is trial#64 with value: 0.7177.


[I 2020-04-06 12:29:12,911] Finished trial#98 with value: 0.6383 with parameters: {'weight_decay': 1.1469784483259161e-07, 'adam_lr': 2.4766802495285115e-05}. Best is trial#64 with value: 0.7177.


[I 2020-04-06 12:29:54,959] Finished trial#99 with value: 0.6868000000000001 with parameters: {'weight_decay': 5.761844180658738e-07, 'adam_lr': 1.242083541337969e-05}. Best is trial#64 with value: 0.7177.


In [28]:
study.best_params

{'adam_lr': 1.0037439813831605e-05, 'weight_decay': 1.947236250600266e-07}

In [29]:
study.best_value

0.7177

In [30]:
study.best_trial

FrozenTrial(number=64, value=0.7177, datetime_start=datetime.datetime(2020, 4, 6, 12, 4, 5, 30696), datetime_complete=datetime.datetime(2020, 4, 6, 12, 4, 49, 38942), params={'weight_decay': 1.947236250600266e-07, 'adam_lr': 1.0037439813831605e-05}, distributions={'weight_decay': LogUniformDistribution(high=0.001, low=1e-10), 'adam_lr': LogUniformDistribution(high=0.1, low=1e-05)}, user_attrs={}, system_attrs={}, intermediate_values={}, trial_id=64, state=TrialState.COMPLETE)

In [36]:
study.trials

[FrozenTrial(number=0, value=0.6414, datetime_start=datetime.datetime(2020, 4, 6, 11, 15, 1, 717927), datetime_complete=datetime.datetime(2020, 4, 6, 11, 15, 51, 596217), params={'weight_decay': 0.00026530122589646306, 'adam_lr': 2.0771766203128445e-05}, distributions={'weight_decay': LogUniformDistribution(high=0.001, low=1e-10), 'adam_lr': LogUniformDistribution(high=0.1, low=1e-05)}, user_attrs={}, system_attrs={}, intermediate_values={}, trial_id=0, state=TrialState.COMPLETE),
 FrozenTrial(number=1, value=0.3526, datetime_start=datetime.datetime(2020, 4, 6, 11, 15, 51, 598676), datetime_complete=datetime.datetime(2020, 4, 6, 11, 16, 40, 411158), params={'weight_decay': 1.3596455127920273e-06, 'adam_lr': 0.009504140289128849}, distributions={'weight_decay': LogUniformDistribution(high=0.001, low=1e-10), 'adam_lr': LogUniformDistribution(high=0.1, low=1e-05)}, user_attrs={}, system_attrs={}, intermediate_values={}, trial_id=1, state=TrialState.COMPLETE),
 FrozenTrial(number=2, value=

In [35]:
study.trials_dataframe()

number   value  ... params_weight_decay     state
0        0  0.6414  ...        2.653012e-04  COMPLETE
1        1  0.3526  ...        1.359646e-06  COMPLETE
2        2  0.4271  ...        5.108506e-10  COMPLETE
3        3  0.5511  ...        1.849624e-09  COMPLETE
4        4  0.6436  ...        8.229798e-09  COMPLETE
..     ...     ...  ...                 ...       ...
95      95  0.6705  ...        1.551026e-08  COMPLETE
96      96  0.7092  ...        6.276030e-07  COMPLETE
97      97  0.3832  ...        7.243300e-07  COMPLETE
98      98  0.6383  ...        1.146978e-07  COMPLETE
99      99  0.6868  ...        5.761844e-07  COMPLETE

[100 rows x 7 columns]